# Solving the Number Partitioning Problem

In this notebook, we will describe how to solve the **Number Partitioning** problem with LunaSolve. We will begin by defining, explaining and giving an example for the Number Partitioning problem. We will then continue by modeling a problem instance, optimize it and implement the solution using LunaSolve. Finally, we will also take a further look at the interpretation of the answer we are returned from Luna.


## Table of Contents

1. [Introduction](#1)
2. [Real World Example](#2)
3. [Solving the Number Partitioning problem with Luna](#3)



<a id="1"></a>
## 1. Introduction

## **Number Partitioning** 

The Number Partitioning problem is a classic combinatorial optimization challenge in computer science and mathematics. It involves dividing a set of numbers into subsets that satisfy specific criteria, often aiming for balance or equality among the subsets. This problem has applications in various fields, including resource allocation, load balancing, and scheduling.

Formally defined, given a set of n positive integers $S={a1 ,a2 ,a3 ,…,an }$, the Number Partitioning problem aims to find a partition of the set of numbers $S$ into two subsets $S_1$ and $S_2$ such that the difference of their respective sums is minimized.

In other words, the objective is to minimize the absolute difference between the sums of the two subsets.

<a id="2"></a>
## 2. Description

An example can be the management of a team of workers tasked with completing a set of jobs. Each job requires a certain amount of time to finish. Your goal is to assign these jobs to the workers in such a way that the workload is distributed as evenly as possible between them. This scenario encapsulates the essence of the Number Partitioning problem: we are trying to distribute a set of numbers (job durations) into two subsets (two workers) to achieve balanced sums (workloads).

Imagine you are managing a team of two workers tasked with completing a set of eight jobs.

Workers 1 and 2 have to complete together the jobs = {8,7,6,5,5,4,3,2}, where the number represents the duration of the job.

<a id="3"></a>
## 3. Solving the Number Partitioning problem with Luna

To follow along with the next steps, the **luna-quantum** library is needed for encoding and solving our optimization problem.

The cell below installs these packages for you if they are not already installed.

In [1]:
# Install dependencies
%pip install --upgrade pip
%pip install luna-quantum --upgrade

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


### 3.1 Set up Luna Client
Now, let's walk through the implementation of the Minimum Vertex Cover problem using LunaSolve. First, create an encryption key. You can generate a key [here](https://docs.aqarios.com/get-started#luna-encryption).

In [2]:
import os
os.environ["LUNA_ENCRYPTION_KEY"] = "<gzaUL8hDECWXRcGrJiEa5wVWVgt4sgPbBDjKN8I92ps>"

As the next step, instantiate a LunaSolve object and set your credentials. The API key is needed to identify you and grant access to the Luna platform. You can find it in your Aqarios account settings.

In [3]:
from luna_sdk import LunaSolve
ls = LunaSolve(api_key="60360df4e8b54305aababfa6ac99429e")

### 3.2 Create a Number Partitioning problem

To create a Number Partitioning instance any list containing different numbers suffices. As aforementioned, the numbers in our list represent the durations of each of the eight jobs.


In [4]:
# List of job durations (in hours)
job_durations = [8, 7, 6, 5, 5, 4, 3, 2]

### 3.3 Creating a Number Partitioning Object

To find the best partition of the set of numbers using LunaSolve, we define the Number Partitioning use case using Luna’s `NumberPartitioning` class. This class takes the job durations and converts them into a QUBO optimization problem of the Number Partitioning problem, which Luna can then optimize.

In [5]:
# import the NumberPartitioning object from the luna sdk
from luna_sdk.schemas import NumberPartitioning

# create a NumberPartitioning object
number_partition = NumberPartitioning(numbers=job_durations)

### 3.4 Create Luna Optimization

We can now upload the problem instance as an optimization to Luna and solve it afterwards.

In [6]:
optimization = ls.optimization.create_from_use_case(name="Number Partition", use_case=number_partition)

### 3.5 Create a Luna Solution

The next step involves creating a job, which is an outbound request to the hardware provider to solve the optimisation problem. By calling the `ls.solution.create()` method of LunaSolve we can create the outbound job. This method takes care of optimizing our problem. To solve the Max Independent Set problem, we pass the `optimization_id` from our optimisation object of our use case, specify the `solver_name` we choose, the `provider` of the computing hardware, `solver_parameters` (which may be specific to the solver), and a `qpu_token` if needed.

In this instance, we solve the Max Independent Set problem using simulated annealing (sa) and choose D-Wave (dwave) as the hardware provider.

In [7]:
job = ls.solution.create(
    optimization_id=optimization.id,
    solver_name="sa",
    provider="dwave",
    solver_parameters={}
)

### 3.6 Retrieve the Solution

In step 3.4, we uploaded the problem, and in 3.5, we made a solve request to Luna. Luna sends the optimisation problem to the provider specified and is returned a solution. Luna autonomously takes care of all background activities, during which the user can turn to other of their important matters. The background processes include the creation and translation of the optimisation problem for the according hardware provider, sending out the request and obtaining a result back, and translating the solution back to an interpretable format.

The `Solution` object created, has multiple attributes expressing different factors of the optimisation problem. These include meta data of the optimisation and the sampled results. The optimisation meta data includes information attached to the use case problem, such as `id`, `name`, `solver`and `provider` names, `runtime` and `qpu` type. Lastly, the `status` variable indicates if the job has been successfully executed and returned to Luna. If the status variable says DONE, the optimisation has finished. In the case REQUESTED is displayed for the status, your optimisation is still being processed. Wait a little bit and re-execute the cell, to retrieve the updated solution.

In [10]:
solution = ls.solution.get(solution_id=job.id)
print(solution)

id: 67b430c0eb1684bd2621c842
name: Number Partition
status: DONE
solver: SA
provider: dwave
runtime:
    total: 0.00786905805580318
    qpu: None
optimization_name: QUBO_MATRIX
created_date: 2025-02-18 07:03:28 (+07)
results:
1 results found. Displaying first 5 results.
Result 1:
    {'sample': {'x0': 1.0, 'x1': 0.0, 'x2': 1.0, 'x3': 0.0, 'x4': 1.0, 'x5': 0.0, 'x6': 0.0, 'x7': 0.0}, 'obj_value': -399.0, 'feasible': True, 'constrain   ....

sense: min
results: [{'representation': {'sets': [[8, 6, 5], [7, 5, 4, 3, 2]], 'sums': [19, 21], 'diff': 2}, 'obj_value': -399.0}]
description: The solution consists of a dict where 'sets' stores an array of length two containing the respective sets of numbers assigned by the solution. 'sums' is an int array of length two containing the sum of each set and 'diff' contains the absolute difference between the sums of each set.

representation={'sets': [[8, 6, 5], [7, 5, 4, 3, 2]], 'sums': [19, 21], 'diff': 2} obj_value=-399.0


Because we converted the use case into the QUBO format, the solution we are returned from our provider is also in this format, which typically is in a vectorised form. However, the encoding from our original optimisation problem might be different. Slack variables, linearisations and transformations between optimisation formats can alter the variable description of optimisation methods. As aforementioned, Luna performs a post-processing step which transforms the solution from the QUBO domain back to a more intuitive domain. 

The `ls.solution.get_use_case_representation(solution_id=job.id)` method transforms the solution of our optimisation to a readable format. The `sense`attribute informs us if we are trying to maximize or minimize our objective function. The `result` is typically given as an iterable containing the `representation` which contains the solution, and the `òbj_value`. The objective value is difficult to interpret as it encompasses both optimization values and constraint penalties, however smaller values express better solutions. The `description` explains the encoding of the `representation` of the result. 

The formal definition of the Number Partitioning problem, the variables $x_i$ represent the number $a_i$ from the family $S$ in the same order as given in our list. If the decision value of $x_i$ is equal to one, then the number with index $i$ is part of the subset $S_1$, while zero means that it is part of the $S_2$ subset.

Accordingly, the representation in the case of the Number Partitioning problem, is a tuple of two lists. Each list contains the indices of all numbers allocated to each of the two partitions.

In [ ]:
use_case_repr = ls.solution.get_use_case_representation(job.id)
print(best_solution)

Finally, if we wish to see the best solution from all evaluated samples we can call the `ls.solution.get_best_use_case_result(use_case_representation=use_case_repr)` method.

In [ ]:
best_solution = ls.solution.get_best_use_case_result(use_case_repr)
print(use_case_repr)